# ExistentialQuantification

> Juan Pablo Yamamoto  
> jpyamamoto\[at\]ciencias.unam.mx  
> Lógica Computacional II. Semestre 2025-1.

Supongamos que queremos desarrollar una lista de cosas cuyo punto en común es la pertenencia a una clase.

Por ejemplo, desarrollemos una lista de cosas que pueden imprimirse (instancias de `Show`).

In [1]:
listaShow = [1, 'a', "hola"]

: 

Listas "heterogéneas" con cuantificación explícita:

In [2]:
{-# LANGUAGE ExistentialQuantification #-}

In [3]:
data Showable = forall a. (Show a) => MkShowable a

In [4]:
listaShow = [MkShowable 1, MkShowable 'a', MkShowable "hola"]

In [5]:
concatShowables :: [Showable] -> String
concatShowables [] = ""
concatShowables [MkShowable x] = show x
concatShowables (MkShowable x : xs) = show x ++ ", " ++ concatShowables xs

In [6]:
concatShowables listaShow

"1, 'a', \"hola\""

## Existencial como Universal

En el curso se ha visto la siguiente equivalencia en el segundo orden:
$$ \exists x . B \equiv \forall y . (\forall x . B \to y) \to y $$

Otra alternativa que es más manejable es la siguiente:

$$ (\exists x . P(x)) \to B \equiv \forall x . P(x)\to B $$

## Sintaxis GADT's

In [7]:
{-# LANGUAGE GADTs #-}

In [8]:
data Showable' where
    MkShowable' :: Show a => a -> Showable'

In [9]:
listaShow' = [MkShowable' 1, MkShowable' 'a', MkShowable' "hola"]

In [10]:
concatShowables' :: [Showable'] -> String
concatShowables' [] = ""
concatShowables' [MkShowable' x] = show x
concatShowables' (MkShowable' x : xs) = show x ++ ", " ++ concatShowables' xs

In [11]:
concatShowables' listaShow'

"1, 'a', \"hola\""

## Generalizando

Con lo anterior, es necesario definir un tipo de dato existencial manualmente por cada caso de interés.

Intentemos realizar un existencial general.

In [12]:
{-# LANGUAGE ConstraintKinds #-}
{-# LANGUAGE TypeApplications #-}

In [13]:
import Data.Kind (Constraint, Type)

In [14]:
data Some (c :: Type -> Constraint) where
    Some :: c a => a -> Some c

In [15]:
existsShow1 :: Some Show
existsShow1 = Some @Show (9 :: Int)

existsShow2 :: Some Show
existsShow2 = Some @Show "Haskell"

In [16]:
:t existsShow1

existsShow1 :: Some Show

In [17]:
:t existsShow2

existsShow2 :: Some Show

In [18]:
showShowable :: Some Show -> String
showShowable (Some x) = show x

In [19]:
showShowable existsShow1

"9"

In [20]:
showShowable existsShow2

"\"Haskell\""

## Records

Los tipos existenciales pueden ser de mucha utilidad para definir ciertos "módulos" cuyo comportamiento permanece oculto. Análogo a instancias de una interfaz.

In [21]:
data Counter a = forall self . NewCounter
    { _this    :: self
    , _inc     :: self -> self
    , _display :: self -> IO ()
    , tag      :: a
    }

In [22]:
inc :: Counter a -> Counter a
inc (NewCounter x inc display tag') = NewCounter
    { _this = inc x, _inc = inc, _display = display, tag = tag' }

display :: Counter a -> IO ()
display NewCounter{ _this = x, _display = display } = display x

In [23]:
counterInt :: Counter String
counterInt = NewCounter
    { _this = 0, _inc = (1+), _display = print, tag = "Ints" }

counterDots :: Counter String
counterDots = NewCounter
    { _this = "", _inc = ('.':), _display = putStrLn, tag = "Dots" }

In [24]:
do
    display (inc counterInt)
    display (inc (inc counterDots))
    putStrLn $ tag counterInt
    putStrLn $ tag counterDots

1
..
Ints
Dots